In [1]:
from bs4 import BeautifulSoup
import pymysql
import time
import re
import pandas as pd
import numpy as np
import os
import math
from tqdm import tqdm

from selenium import webdriver
from selenium.common.exceptions import ElementNotInteractableException
from selenium.common.exceptions import NoSuchElementException
from selenium.webdriver.common.keys import Keys

In [2]:
##### 파라미터
param_list_gu = ['마포구','서대문구','은평구','종로구','중구','용산구','성동구','광진구',
                 '동대문구','성북구','강북구','도봉구','노원구','중랑구','강동구','송파구',
                 '강남구','서초구','관악구','동작구','영등포구','금천구','구로구','양천구','강서구']

##### 데이터 프레임
df = pd.DataFrame(columns = ["구 이름","가게이름","가게주소","별점","가게링크"])

In [14]:
for gu in param_list_gu:
    options = webdriver.ChromeOptions()
    # options.add_argument('headless')
    options.add_argument("Mozilla/5.0")
    options.add_argument('lang=ko_KR')
    chromedriver_path = "./chromedriver.exe"
    driver = webdriver.Chrome(os.path.join(os.getcwd(), chromedriver_path), options=options)  # chromedriver 열기
    driver.get('https://map.kakao.com/')  # 주소 가져오기
    search_area = driver.find_element_by_xpath('//*[@id="search.keyword.query"]') # 검색 창
    search_area.send_keys(gu + ' 맛집')  # 검색어 입력
    
    driver.find_element_by_xpath('//*[@id="search.keyword.submit"]').send_keys(Keys.ENTER)  # Enter로 검색
    driver.implicitly_wait(3) # 기다려 주자
    more_page = driver.find_element_by_id("info.search.place.more")
    # more_page.click()
    more_page.send_keys(Keys.ENTER) # 더보기 누르고
    # 첫 번째 검색 페이지 끝
    # driver.implicitly_wait(5) # 기다려 주자
    time.sleep(1)
    
        # next 사용 가능?
    next_btn = driver.find_element_by_id("info.search.page.next")
    has_next = "disabled" not in next_btn.get_attribute("class").split(" ")
    Page = 1
    while has_next: # 다음 페이지가 있으면 loop
        time.sleep(1)
        # place_lists = driver.find_elements_by_css_selector('#info\.search\.place\.list > li:nth-child(1)')
        # 페이지 루프
        #info\.search\.page\.no1 ~ .no5
        page_links = driver.find_elements_by_css_selector("#info\.search\.page a")
        pages = [link for link in page_links if "HIDDEN" not in link.get_attribute("class").split(" ")]
        # print(len(pages), "개의 페이지 있음")
        # pages를 하나씩 클릭하면서
        for i in range(1, 6):
            xPath = '//*[@id="info.search.page.no' + str(i) + '"]'
            try:
                page = driver.find_element_by_xpath(xPath)
                page.send_keys(Keys.ENTER)
            except ElementNotInteractableException:
                print('End of Page')
                break;
            time.sleep(3)
            place_lists = driver.find_elements_by_css_selector('#info\.search\.place\.list > li')
            for p in place_lists: # WebElement
                # print(p.get_attribute('innerHTML'))
                # print("type of p:", type(p))
                store_html = p.get_attribute('innerHTML')
                store_info = BeautifulSoup(store_html, "html.parser")
                # BS -> 분석
                #
                place_name = store_info.select('.head_item > .tit_name > .link_name')
                # place_address = store_info.select('.info_item > .addr > p')
                # place_hour = store_info.select('.info_item > .openhour > p > a')
                # place_tel = store_info.select('.info_item > .contact > span')
                 # print("length:", len(place_name))
                if len(place_name) == 0:
                    continue # 광고
                place_name = store_info.select('.head_item > .tit_name > .link_name')[0].text
                place_address = store_info.select('.info_item > .addr > p')[0].text
                place_score = store_info.select('.rating > .score > em')[0].text
                place_link = store_info.select('.info_item > .contact > a')[0]["href"]
                
                print(place_name)
                print("-"*70)
                print(place_address)
                print("-"*70)
                print(place_score)
                print("-"*70)
                print(place_link)
                
                data_to_insert = {'구 이름' : gu, "가게이름" : place_name,
                                  "가게주소" : place_address, "별점" : place_score,
                                  "가게링크" : place_link}
                df = df.append(data_to_insert, ignore_index=True)
        
        print(df)
        next_btn = driver.find_element_by_id("info.search.page.next")
        has_next = "disabled" not in next_btn.get_attribute("class").split(" ")
        if not has_next:
            print('Arrow is Disabled')
            driver.close()
            break # 다음 페이지 없으니까 종료
        else: # 다음 페이지 있으면
            Page += 1
            next_btn.send_keys(Keys.ENTER)
    print("End of Crawl")

피오니 홍대점
----------------------------------------------------------------------
서울 마포구 독막로7길 51 1층
----------------------------------------------------------------------
3.8
----------------------------------------------------------------------
https://place.map.kakao.com/26235884
어반플랜트
----------------------------------------------------------------------
서울 마포구 독막로4길 3 1,2층
----------------------------------------------------------------------
4.2
----------------------------------------------------------------------
https://place.map.kakao.com/447132083
프릳츠 도화점
----------------------------------------------------------------------
서울 마포구 새창로2길 17
----------------------------------------------------------------------
3.9
----------------------------------------------------------------------
https://place.map.kakao.com/24529429
크레이지카츠
----------------------------------------------------------------------
서울 마포구 포은로2나길 44
-----------------------------------------------------------------

우리바다수산
----------------------------------------------------------------------
서울 마포구 월드컵로 102
----------------------------------------------------------------------
3.9
----------------------------------------------------------------------
https://place.map.kakao.com/15965312
943킹스크로스
----------------------------------------------------------------------
서울 마포구 양화로16길 24
----------------------------------------------------------------------
3.7
----------------------------------------------------------------------
https://place.map.kakao.com/53292857
정돈
----------------------------------------------------------------------
서울 마포구 어울마당로 46 1층
----------------------------------------------------------------------
4.5
----------------------------------------------------------------------
https://place.map.kakao.com/90725902
테이스티버거
----------------------------------------------------------------------
서울 마포구 독막로 67-11 행운빌딩 1층
----------------------------------------------------------------

서울 마포구 백범로25길 9
----------------------------------------------------------------------
3.3
----------------------------------------------------------------------
https://place.map.kakao.com/7990640
몰토베네
----------------------------------------------------------------------
서울 마포구 성지3길 67 1층
----------------------------------------------------------------------
4.4
----------------------------------------------------------------------
https://place.map.kakao.com/926080103
당인리책발전소
----------------------------------------------------------------------
서울 마포구 월드컵로14길 10-8 1층
----------------------------------------------------------------------
3.5
----------------------------------------------------------------------
https://place.map.kakao.com/123575123
원조조박집 본관
----------------------------------------------------------------------
서울 마포구 토정로 313-1
----------------------------------------------------------------------
4.1
------------------------------------------------------------------

테일러커피 서교점
----------------------------------------------------------------------
서울 마포구 와우산로27길 7 2층
----------------------------------------------------------------------
4.3
----------------------------------------------------------------------
https://place.map.kakao.com/27248379
딥블루레이크&커피로스터스
----------------------------------------------------------------------
서울 마포구 포은로6길 11
----------------------------------------------------------------------
4.2
----------------------------------------------------------------------
https://place.map.kakao.com/27481601
잇텐고
----------------------------------------------------------------------
서울 마포구 포은로 11
----------------------------------------------------------------------
4.0
----------------------------------------------------------------------
https://place.map.kakao.com/1992580850
굴다리식당
----------------------------------------------------------------------
서울 마포구 새창로 8-1
------------------------------------------------------------------

얼스어스
----------------------------------------------------------------------
서울 마포구 성미산로 150
----------------------------------------------------------------------
3.7
----------------------------------------------------------------------
https://place.map.kakao.com/111850276
돈카츠윤석
----------------------------------------------------------------------
서울 마포구 백범로10길 30 1층
----------------------------------------------------------------------
3.8
----------------------------------------------------------------------
https://place.map.kakao.com/692466501
이치류 홍대본점
----------------------------------------------------------------------
서울 마포구 잔다리로3안길 44
----------------------------------------------------------------------
4.1
----------------------------------------------------------------------
https://place.map.kakao.com/19083939
지로우라멘
----------------------------------------------------------------------
서울 마포구 와우산로29가길 79
------------------------------------------------------------------

...

다루마
----------------------------------------------------------------------
서울 강서구 마곡중앙5로1길 21 럭스나인오피스텔 N동 2층 201호
----------------------------------------------------------------------
5.0
----------------------------------------------------------------------
https://place.map.kakao.com/151463780
홍차이 발산본점
----------------------------------------------------------------------
서울 강서구 마곡중앙8로 90 마곡아이파크 2층
----------------------------------------------------------------------
3.7
----------------------------------------------------------------------
https://place.map.kakao.com/512708789
      구 이름        가게이름                                    가게주소   별점  \
0      마포구     피오니 홍대점                      서울 마포구 독막로7길 51 1층  3.8   
1      마포구       어반플랜트                     서울 마포구 독막로4길 3 1,2층  4.2   
2      마포구     프릳츠 도화점                         서울 마포구 새창로2길 17  3.9   
3      마포구      크레이지카츠                        서울 마포구 포은로2나길 44  3.9   
4      마포구         미쁘동                  서울 마포구 동교로38길 33

미스터피자 발산점
----------------------------------------------------------------------
서울 강서구 강서로 289 연빌딩 1층 101호
----------------------------------------------------------------------
3.5
----------------------------------------------------------------------
https://place.map.kakao.com/1187045033
서가앤쿡 서울마곡점
----------------------------------------------------------------------
서울 강서구 마곡동로 55 마커스빌딩 2층
----------------------------------------------------------------------
3.1
----------------------------------------------------------------------
https://place.map.kakao.com/1887425154
피맥하우스 마곡점
----------------------------------------------------------------------
서울 강서구 마곡중앙6로 45
----------------------------------------------------------------------
4.0
----------------------------------------------------------------------
https://place.map.kakao.com/1056575807
늘상식당 강서구청점
----------------------------------------------------------------------
서울 강서구 화곡로58길 22-14
-------------------------------

천사곱창 마곡나루점
----------------------------------------------------------------------
서울 강서구 마곡중앙로 161-8 두산더랜드파크 1층 C동 117호
----------------------------------------------------------------------
2.1
----------------------------------------------------------------------
https://place.map.kakao.com/720776696
밀회관 마곡나루점
----------------------------------------------------------------------
서울 강서구 마곡중앙로 161-11 1층
----------------------------------------------------------------------
3.3
----------------------------------------------------------------------
https://place.map.kakao.com/1394011703
안주공방
----------------------------------------------------------------------
서울 강서구 국회대로 85-41 1층
----------------------------------------------------------------------
4.6
----------------------------------------------------------------------
https://place.map.kakao.com/224568719
이모네돼지갈비
----------------------------------------------------------------------
서울 강서구 화곡로60길 26 1층
---------------------------

춘천무쇠닭갈비 까치산역점
----------------------------------------------------------------------
서울 강서구 곰달래로 147-1
----------------------------------------------------------------------
2.6
----------------------------------------------------------------------
https://place.map.kakao.com/17102982
곰돌생소금구이
----------------------------------------------------------------------
서울 강서구 곰달래로 227
----------------------------------------------------------------------
5.0
----------------------------------------------------------------------
https://place.map.kakao.com/16046177
아프리카커피
----------------------------------------------------------------------
서울 강서구 공항대로46길 89
----------------------------------------------------------------------
3.0
----------------------------------------------------------------------
https://place.map.kakao.com/20943339
대청도자연산식당
----------------------------------------------------------------------
서울 강서구 강서로 455 마곡경동미르웰 102동 107호
--------------------------------------------

5.0
----------------------------------------------------------------------
https://place.map.kakao.com/10123314
피쉬앤스시 염창점
----------------------------------------------------------------------
서울 강서구 양천로 690 1층
----------------------------------------------------------------------
3.2
----------------------------------------------------------------------
https://place.map.kakao.com/545787988
남도복국 등촌점
----------------------------------------------------------------------
서울 강서구 강서로56길 102 1층
----------------------------------------------------------------------
3.3
----------------------------------------------------------------------
https://place.map.kakao.com/1045469928
조개깡패연구소 발산역마곡점
----------------------------------------------------------------------
서울 강서구 공항대로 269-15 마곡힐스테이트에코오피스텔 1층 113호
----------------------------------------------------------------------
2.0
----------------------------------------------------------------------
https://place.map.kakao.com/1699144433
교촌치킨 마곡

In [15]:
df.to_csv("./data/kakao_store.csv", encoding="utf-8")

df

구 이름            가게이름                                      가게주소   별점  \
0      마포구         피오니 홍대점                        서울 마포구 독막로7길 51 1층  3.8   
1      마포구           어반플랜트                       서울 마포구 독막로4길 3 1,2층  4.2   
2      마포구         프릳츠 도화점                           서울 마포구 새창로2길 17  3.9   
3      마포구          크레이지카츠                          서울 마포구 포은로2나길 44  3.9   
4      마포구             미쁘동                    서울 마포구 동교로38길 33-21 2층        
...    ...             ...                                       ...  ...   
12518  강서구        남도복국 등촌점                      서울 강서구 강서로56길 102 1층  3.3   
12519  강서구  조개깡패연구소 발산역마곡점  서울 강서구 공항대로 269-15 마곡힐스테이트에코오피스텔 1층 113호  2.0   
12520  강서구       교촌치킨 마곡역점                           서울 강서구 공항대로 209  4.5   
12521  강서구          등촌정육식당                 서울 강서구 공항대로59길 75 나동 1~2층  3.4   
12522  강서구           동래순훠궈            서울 강서구 마곡중앙6로 93 열린프라자 3층 307호  4.8   

                                         가게링크  
0        https://place.map.kakao.com/26235884  
1       https://place.map.kakao.com/447132083  
2        https://place.map.kakao.com/24529429  
3        https://place.map.kakao.com/83301316  
4      https://place.map.kakao.com/1087043762  
...                                       ...  
12518  https://place.map.kakao.com/1045469928  
12519  https://place.map.kakao.com/1699144433  
12520  https://place.map.kakao.com/1279093277  
12521  https://place.map.kakao.com/1823221194  
12522  https://place.map.kakao.com/1785400276  

[12523 rows x 5 columns]

In [3]:
##### LOAD DATAFRAME
df = pd.read_csv("./data/kakao_store.csv", index_col=0)
df

구 이름            가게이름                                      가게주소   별점  \
0      마포구         피오니 홍대점                        서울 마포구 독막로7길 51 1층  3.8   
1      마포구           어반플랜트                       서울 마포구 독막로4길 3 1,2층  4.2   
2      마포구         프릳츠 도화점                           서울 마포구 새창로2길 17  3.9   
3      마포구          크레이지카츠                          서울 마포구 포은로2나길 44  3.9   
4      마포구             미쁘동                    서울 마포구 동교로38길 33-21 2층  NaN   
...    ...             ...                                       ...  ...   
12518  강서구        남도복국 등촌점                      서울 강서구 강서로56길 102 1층  3.3   
12519  강서구  조개깡패연구소 발산역마곡점  서울 강서구 공항대로 269-15 마곡힐스테이트에코오피스텔 1층 113호  2.0   
12520  강서구       교촌치킨 마곡역점                           서울 강서구 공항대로 209  4.5   
12521  강서구          등촌정육식당                 서울 강서구 공항대로59길 75 나동 1~2층  3.4   
12522  강서구           동래순훠궈            서울 강서구 마곡중앙6로 93 열린프라자 3층 307호  4.8   

                                         가게링크  
0        https://place.map.kakao.com/26235884  
1       https://place.map.kakao.com/447132083  
2        https://place.map.kakao.com/24529429  
3        https://place.map.kakao.com/83301316  
4      https://place.map.kakao.com/1087043762  
...                                       ...  
12518  https://place.map.kakao.com/1045469928  
12519  https://place.map.kakao.com/1699144433  
12520  https://place.map.kakao.com/1279093277  
12521  https://place.map.kakao.com/1823221194  
12522  https://place.map.kakao.com/1785400276  

[12523 rows x 5 columns]

In [62]:
# columns = ['score', 'review']
# review_df = pd.DataFrame(columns=columns)
# review_df는 중간에 한번 끊겨서 아래 셀에서 다시 불러옴

stars=[]
reviews=[]

for link in tmp_df.iloc[:,0]:
    print(link)
    driver = webdriver.Chrome(executable_path="./chromedriver.exe")
    driver.get(link)

    last_height = driver.execute_script("return document.body.scrollHeight")

    while True:

        driver.execute_script("window.scrollTo(0, document.body.scrollHeight);")

        time.sleep(2)

                # 스크롤 다운 후 스크롤 높이 다시 가져옴
        new_height = driver.execute_script("return document.body.scrollHeight")
        if new_height == last_height:
            break
        last_height = new_height

        tmp=driver.page_source
        tmp2 = BeautifulSoup(tmp, "html.parser")

        tmp3 = tmp2.select('#mArticle > div.cont_evaluation > strong.total_evaluation > span.color_b')
        
        if len(tmp3) == 0:
            print("넘어감")
            continue
        else:
            total_reviews=int(tmp2.select('#mArticle > div.cont_evaluation > strong.total_evaluation > span.color_b')[0].get_text())
            pages=math.ceil(total_reviews/5)
            print(pages)
            time.sleep(5)
            
    if len(tmp3) == 0:
        print("리뷰 없으므로 넘어감")
        driver.close()
        continue
    else:
        for i in range(1,pages+1):
            t1=driver.page_source
            t2=BeautifulSoup(t1, "html.parser")
            t3=t2.find(name="div", attrs={"class":"evaluation_review"})

            star=t3.find_all('em',{'class':'num_rate'})
            review=t3.find_all('p',{'class':'txt_comment'})
            
            stars.extend(star)
            reviews.extend(review)
            
            i=i+1

            if i > pages:
                break

            next_page = driver.find_element_by_xpath("//a[@data-page='" + str(i) + "']")
            next_page.send_keys(Keys.ENTER)
            time.sleep(5)

        driver.close()
        
    for s, r in zip(stars, reviews):
        row = [s.text[0], r.find(name="span").text]
        series = pd.Series(row, index=review_df.columns)
        review_df = review_df.append(series, ignore_index=True)
    
    review_df.to_csv('review_df.csv',encoding='utf-8')

https://place.map.kakao.com/22446604
7
https://place.map.kakao.com/1248819302
11
https://place.map.kakao.com/27281186
8
https://place.map.kakao.com/22895023
17
https://place.map.kakao.com/561010883
25
https://place.map.kakao.com/26611450
15
https://place.map.kakao.com/8105623
15
https://place.map.kakao.com/1641347883
23
https://place.map.kakao.com/2123242037
18
https://place.map.kakao.com/10341266
7
https://place.map.kakao.com/805500797
8
https://place.map.kakao.com/780523213
6
https://place.map.kakao.com/1689615887
20
https://place.map.kakao.com/26966117
24
https://place.map.kakao.com/406052128
8
https://place.map.kakao.com/1246652450
3
https://place.map.kakao.com/607192266
18
https://place.map.kakao.com/299792247
7
https://place.map.kakao.com/1819203967
22
https://place.map.kakao.com/1829215556
9
https://place.map.kakao.com/13091834
8
https://place.map.kakao.com/795074926
14
https://place.map.kakao.com/2078186665
7
https://place.map.kakao.com/27315733
10
https://place.map.kakao.com/1

KeyboardInterrupt: 

In [ ]:
        total_reviews = tmp2.find_all("p", {"class":"txt_comment"})
        total_score = tmp2.find_all("em", {"class":"num_rate"})
        print(total_score)
        print(total_reviews)
        for reviews in total_reviews:
            review = reviews.get_text()[:-3]
            print(review)
            
        score_cnt = 0
        for score in total_score:
            if score_cnt > 1:
                store_score = re.findall(r"\d+",score.get_text())[0]
                print(store_score)
            
            score_cnt+=1

In [51]:
review_df = pd.read_csv("./review_df.csv", encoding="utf-8", index_col = 0)

In [52]:
review_df

score                                             review
0           4  생크림이 좀더 듬뿍 올라가고, 시트가 더 부드러우면 더 맛있을거같다 우유향이 나고 ...
1           4                                                굿굿!
2           4                                               맛있어요
3           5                                               맛있어요
4           1  진짜 유명해서 한번 먹어봄 생딸기가 아니고 절임딸기 한조각 6300원 시트도 퍼석하...
...       ...                                                ...
972563      3  몇년전 초창기일때보다 양은 줄었지만 (물가가올랐으니) 그래도 평타는 하는집. 분위기...
972564      4  烤腸吃到飽！ ₩21900韓元 $590台幣 牛大腸.牛小腸.牛心臟.牛肚.牛胃. 覺得很好...
972565      3                                                NaN
972566      3                                                NaN
972567      3                                                NaN

[972568 rows x 2 columns]

In [21]:
tmp_df = df.copy()

tmp_df.set_index("가게링크", inplace=True)

In [22]:
tmp_df = tmp_df.loc["https://place.map.kakao.com/8094563":,:]
tmp_df.reset_index(inplace=True)
tmp_df

가게링크  구 이름            가게이름  \
0        https://place.map.kakao.com/8094563  영등포구             진주집   
1     https://place.map.kakao.com/1784717740  영등포구            이한스시   
2     https://place.map.kakao.com/1393296142  영등포구              오돌   
3       https://place.map.kakao.com/10651104  영등포구            영일분식   
4        https://place.map.kakao.com/9125675  영등포구       삼거리먼지막순대국   
...                                      ...   ...             ...   
2492  https://place.map.kakao.com/1045469928   강서구        남도복국 등촌점   
2493  https://place.map.kakao.com/1699144433   강서구  조개깡패연구소 발산역마곡점   
2494  https://place.map.kakao.com/1279093277   강서구       교촌치킨 마곡역점   
2495  https://place.map.kakao.com/1823221194   강서구          등촌정육식당   
2496  https://place.map.kakao.com/1785400276   강서구           동래순훠궈   

                                          가게주소   별점  
0               서울 영등포구 국제금융로6길 33 여의도백화점 지하1층  3.8  
1                     서울 영등포구 선유로22길 3 유선빌딩 2층  3.2  
2                         서울 영등포구 국회대로37길 6 1층  4.0  
3                        서울 영등포구 도림로141가길 34-1  3.5  
4                          서울 영등포구 시흥대로185길 11  4.2  
...                                        ...  ...  
2492                      서울 강서구 강서로56길 102 1층  3.3  
2493  서울 강서구 공항대로 269-15 마곡힐스테이트에코오피스텔 1층 113호  2.0  
2494                           서울 강서구 공항대로 209  4.5  
2495                 서울 강서구 공항대로59길 75 나동 1~2층  3.4  
2496            서울 강서구 마곡중앙6로 93 열린프라자 3층 307호  4.8  

[2497 rows x 5 columns]

In [16]:
# 데이터가 너무 많음.
# 그래서 구마다 리뷰를 다시 뽑고 나중에 리뷰 데이터 합칠 것.
# 각 구마다 30개 가게씩
# reduce_columns = ['가게링크', '구 이름', '가게이름', '가게주소', '별점']
# reduce_df = pd.DataFrame(columns=reduce_columns)

# for gu in tmp_df["구 이름"].unique():
#     reduce_df = pd.concat([tmp_df[tmp_df["구 이름"] == gu].head(30), reduce_df])
    
# reduce_df
for gu in tmp_df["구 이름"].unique():
    reduce_df = tmp_df[tmp_df["구 이름"] == gu].head(30)
    print(reduce_df)

                                      가게링크 구 이름               가게이름  \
0    https://place.map.kakao.com/504832915  마포구       제주은희네해장국 홍대점   
1     https://place.map.kakao.com/36768345  마포구            카페 지금여기   
2     https://place.map.kakao.com/24324645  마포구     오리지널시카고피자 홍대본점   
3     https://place.map.kakao.com/21318949  마포구            성미골고기마을   
4     https://place.map.kakao.com/13311040  마포구  원조양평신내서울해장국 마포직영점   
5   https://place.map.kakao.com/1139784588  마포구           태양커피 홍대점   
6     https://place.map.kakao.com/25044283  마포구           장수갈매기 본점   
7     https://place.map.kakao.com/10941063  마포구              마포왕족발   
8   https://place.map.kakao.com/1843931972  마포구               명인갈비   
9   https://place.map.kakao.com/1652929268  마포구        크라이치즈버거 상암점   
10  https://place.map.kakao.com/1287768129  마포구        크래버대게나라 마포점   
11    https://place.map.kakao.com/27272826  마포구                요코쵸   
12     https://place.map.kakao.com/8507513  마포구               영광보쌈   
13   https://place.m

In [23]:
# 데이터가 너무 많아서 각자 데이터를 만들고
# 합칠 예정
param_list_gu_2 = ['영등포구','금천구','구로구','양천구','강서구']


cnt = 21
for gu in tmp_df["구 이름"].unique():
    if gu in param_list_gu_2:
        columns = ['score', 'review']
        review_df = pd.DataFrame(columns=columns)

        stars=[]
        reviews=[]

        reduce_df = tmp_df[tmp_df["구 이름"] == gu].head(30)

        for link in reduce_df.iloc[:,0]:
            print(link)
            driver = webdriver.Chrome(executable_path="./chromedriver.exe")
            driver.get(link)

            last_height = driver.execute_script("return document.body.scrollHeight")

            while True:

                driver.execute_script("window.scrollTo(0, document.body.scrollHeight);")

                time.sleep(2)

                        # 스크롤 다운 후 스크롤 높이 다시 가져옴
                new_height = driver.execute_script("return document.body.scrollHeight")
                if new_height == last_height:
                    break
                last_height = new_height

                tmp=driver.page_source
                tmp2 = BeautifulSoup(tmp, "html.parser")

                tmp3 = tmp2.select('#mArticle > div.cont_evaluation > strong.total_evaluation > span.color_b')

                if len(tmp3) == 0:
                    print("넘어감")
                    continue
                else:
                    total_reviews=int(tmp2.select('#mArticle > div.cont_evaluation > strong.total_evaluation > span.color_b')[0].get_text())
                    pages=math.ceil(total_reviews/5)
                    print(pages)
                    time.sleep(5)

            if len(tmp3) == 0:
                print("리뷰 없으므로 넘어감")
                driver.close()
                continue
            else:
                for i in range(1,pages+1):
                    t1=driver.page_source
                    t2=BeautifulSoup(t1, "html.parser")
                    t3=t2.find(name="div", attrs={"class":"evaluation_review"})

                    star=t3.find_all('em',{'class':'num_rate'})
                    review=t3.find_all('p',{'class':'txt_comment'})

                    stars.extend(star)
                    reviews.extend(review)

                    i=i+1

                    if i > pages:
                        break

                    next_page = driver.find_element_by_xpath("//a[@data-page='" + str(i) + "']")
                    next_page.send_keys(Keys.ENTER)
                    time.sleep(5)

                driver.close()

            for s, r in zip(stars, reviews):
                row = [s.text[0], r.find(name="span").text]
                series = pd.Series(row, index=review_df.columns)
                review_df = review_df.append(series, ignore_index=True)

        review_df.to_csv('./data/review_data/review_df_{}.csv'.format(cnt), encoding='utf-8')
        cnt+=1

https://place.map.kakao.com/8094563
55
https://place.map.kakao.com/1784717740
16
https://place.map.kakao.com/1393296142
10
https://place.map.kakao.com/10651104
21
https://place.map.kakao.com/9125675
17
https://place.map.kakao.com/12004662
14
https://place.map.kakao.com/2137940343
16
https://place.map.kakao.com/20746242
25
https://place.map.kakao.com/1142427389
25
https://place.map.kakao.com/8510748
27
https://place.map.kakao.com/1210497999
11
https://place.map.kakao.com/1808171777
15
https://place.map.kakao.com/1247032398
10
https://place.map.kakao.com/409589446
10
https://place.map.kakao.com/21299769
14
https://place.map.kakao.com/2030217673
5
https://place.map.kakao.com/26971510
10
https://place.map.kakao.com/1407569042
5
https://place.map.kakao.com/27221935
12
https://place.map.kakao.com/23493474
14
https://place.map.kakao.com/1456174621
18
https://place.map.kakao.com/1214126801
8
https://place.map.kakao.com/15825589
12
https://place.map.kakao.com/893093723
5
https://place.map.kakao

In [31]:
path = './data/review_data/'
file_list = os.listdir(path)
review_total_data = [file for file in file_list if file.endswith('.csv')]

columns = ['score', 'review']

review_DataFrame = pd.DataFrame(columns = columns)

print(review_total_data)

for review_path in review_total_data:
    rv_df = pd.read_csv("./data/review_data/{}".format(review_path), index_col = 0)
    review_DataFrame = pd.concat([review_DataFrame,rv_df])
    
print(review_DataFrame)

['review_df.csv', 'review_df_10.csv', 'review_df_11.csv', 'review_df_12.csv', 'review_df_13.csv', 'review_df_14.csv', 'review_df_15.csv', 'review_df_16.csv', 'review_df_17.csv', 'review_df_18.csv', 'review_df_19.csv', 'review_df_20.csv', 'review_df_21.csv', 'review_df_22.csv', 'review_df_23.csv', 'review_df_24.csv', 'review_df_25.csv', 'review_df_7.csv', 'review_df_8.csv', 'review_df_9.csv']


C:\Users\USER\anaconda3\lib\site-packages\numpy\lib\arraysetops.py:569: FutureWarning: elementwise comparison failed; returning scalar instead, but in the future will perform elementwise comparison
  mask |= (ar1 == a)


      score                                             review
0         4  생크림이 좀더 듬뿍 올라가고, 시트가 더 부드러우면 더 맛있을거같다 우유향이 나고 ...
1         4                                                굿굿!
2         4                                               맛있어요
3         5                                               맛있어요
4         1  진짜 유명해서 한번 먹어봄 생딸기가 아니고 절임딸기 한조각 6300원 시트도 퍼석하...
...     ...                                                ...
31368     1  자리 넓고 쾌적해서 좋은데 알바분이 너무너무 불친절하네요.. 묻는 말에도 고개만 끄...
31369     5  근래 가본 카페 중에 가장 마음에 들었다 일단 천장이 높아서 확- 트이는 마음! 공...
31370     4  인테리어 시원시원해서 예쁘고 음료도 맛있는 편이에요✔︎  디저트는 조금 비싼 것 같아요~
31371     5                                     좋아요 디저트류도 맛잇어요
31372     2                                                NaN

[4831773 rows x 2 columns]


In [34]:
review_DataFrame.to_csv("./data/review_data/total_review.csv", encoding="utf-8-sig")

In [35]:
review_DataFrame

score                                             review
0         4  생크림이 좀더 듬뿍 올라가고, 시트가 더 부드러우면 더 맛있을거같다 우유향이 나고 ...
1         4                                                굿굿!
2         4                                               맛있어요
3         5                                               맛있어요
4         1  진짜 유명해서 한번 먹어봄 생딸기가 아니고 절임딸기 한조각 6300원 시트도 퍼석하...
...     ...                                                ...
31368     1  자리 넓고 쾌적해서 좋은데 알바분이 너무너무 불친절하네요.. 묻는 말에도 고개만 끄...
31369     5  근래 가본 카페 중에 가장 마음에 들었다 일단 천장이 높아서 확- 트이는 마음! 공...
31370     4  인테리어 시원시원해서 예쁘고 음료도 맛있는 편이에요✔︎  디저트는 조금 비싼 것 같아요~
31371     5                                     좋아요 디저트류도 맛잇어요
31372     2                                                NaN

[4831773 rows x 2 columns]